### Get Dataset from request

In [ ]:
from datetime import datetime as dt
from pathlib import Path

import pandas as pd
import numpy as np

from toargridding.grids import RegularGrid
from toargridding.toar_rest_client import (
    AnalysisServiceDownload,
    STATION_LAT,
    STATION_LON,
)
from toargridding.metadata import Metadata, TimeSample, AnalysisRequestResult, Coordinates
from toargridding.variables import Coordinate


endpoint = "https://toar-data.fz-juelich.de/api/v2/analysis/statistics/"
#starts in directory [path/to/toargridding]/tests
#maybe adopt the toargridding_base_path for your machine.
toargridding_base_path = Path(".")
cache_dir = toargridding_base_path / "cache"
data_download_dir = toargridding_base_path / "data"

analysis_service = AnalysisServiceDownload(endpoint, cache_dir, data_download_dir)
my_grid = RegularGrid(1.9, 2.5)

time = TimeSample(dt(2016,1,1), dt(2016,12,31), "monthly")
metadata = Metadata.construct("mole_fraction_of_ozone_in_air", time, "mean")


In [ ]:
# this cell can runs longer than 30minutes
data = analysis_service.get_data(metadata)
ds = my_grid.as_xarray(data)

### Visual inspection

In [ ]:
#calculation of coordinates for plotting
#especially separation of coordinates with results and without results.

import cartopy.crs as ccrs
import matplotlib.pyplot as plt
import matplotlib.ticker as mticker

mean_data = ds["mean"]
clean_coords = data.stations_coords
all_na = data.stations_data.isna().all(axis=1)
clean_coords = all_na.to_frame().join(clean_coords)[["latitude", "longitude"]]
all_na_coords = clean_coords[all_na]
not_na_coords = clean_coords[~all_na]

In [ ]:
import matplotlib as mpl

#definition of plotting function

def plot_cells(data, stations, na_stations, discrete=True, plot_stations=False):
    fig = plt.figure(figsize=(9, 18))

    ax = plt.axes(projection=ccrs.PlateCarree())
    ax.coastlines()
    gl = ax.gridlines(draw_labels=True)
    gl.top_labels = False
    gl.left_labels = False
    gl.xlocator = mticker.FixedLocator(data.longitude.values)
    gl.ylocator = mticker.FixedLocator(data.latitude.values)

    cmap = mpl.cm.viridis

    if discrete:
        print(np.unique(data.values))
        bounds = np.arange(8)
        norm = mpl.colors.BoundaryNorm(bounds, cmap.N, extend="both")
        ticks = np.arange(bounds.size + 1)[:-1] + 0.5
        ticklables = bounds
        
        im = plt.pcolormesh(
            data.longitude,
            data.latitude,
            data,
            transform=ccrs.PlateCarree(),
            cmap=cmap,
            shading="nearest",
            norm=norm,
        )
        cb = fig.colorbar(im, ax=ax, shrink=0.2, aspect=25)
        cb.set_ticks(ticks)
        cb.set_ticklabels(ticklables)
        im = plt.pcolormesh(
            data.longitude,
            data.latitude,
            data,
            transform=ccrs.PlateCarree(),
            cmap=cmap,
            shading="nearest",
            norm=norm,
        )
    else:
        im = plt.pcolormesh(
            data.longitude,
            data.latitude,
            data,
            transform=ccrs.PlateCarree(),
            cmap=cmap,
            shading="nearest",
        )

        cb = fig.colorbar(im, ax=ax, shrink=0.2, aspect=25)
    

    if plot_stations:
        plt.scatter(na_stations["longitude"], na_stations["latitude"], s=1, c="k")
        plt.scatter(stations["longitude"], stations["latitude"], s=1, c="r")

    plt.tight_layout()

    plt.title(f"global ozon at {data.time.values} {data.time.units}")

In [ ]:
#example visualization for two time points
print(not_na_coords)
timestep = 2
time = ds.time[timestep]
data = ds.sel(time=time)

plot_cells(data["mean"], not_na_coords, all_na_coords, discrete=False, plot_stations=True)
plt.show()

plot_cells(data["n"], not_na_coords, all_na_coords, discrete=True)
plt.show()

n_observations = ds["n"].sum(["latitude", "longitude"])
plt.plot(ds.time, n_observations)
print(np.unique(ds["n"]))

In [ ]:
print(data)